<table>
    <tr>
        <td>
          <img src="../images/ProjectPythia_Logo_Final-01-Blue.svg" width=250 alt="Project Pythia Logo"></img>
        </td>
        <td>
          <img src="../images/ecmwf.png" style="width:250px" alt="ECMWF logo">
        </td>
        <td>
          <img src="../images/googleresearch.png" style="width:250px" alt="Google logo">
        </td>
    </tr>
</table>

# ERA5_ARCO Pressure Level Data Exploration: Matplotlib

---

## Overview
A team at [Google Research & Cloud](https://research.google/) are making parts of the [ECMWF Reanalysis version 5](https://www.ecmwf.int/en/forecasts/dataset/ecmwf-reanalysis-v5) (aka **ERA-5**) accessible in a [Analysis Ready, Cloud Optimized](https://www.frontiersin.org/articles/10.3389/fclim.2021.782909/full) (aka **ARCO**) format.

In this notebook, we will do the following:

1. Access the [ERA-5 ARCO](https://github.com/google-research/arco-era5) catalog
1. Select a particular dataset and variable from the catalog


## Prerequisites

| Concepts | Importance | Notes |
| --- | --- | --- |
| [Cartopy](https://foundations.projectpythia.org/core/cartopy/cartopy.html) | Necessary | |
| [Xarray](https://foundations.projectpythia.org/core/xarray) | Necessary | |


- **Time to learn**: 30 minutes

---

## Imports

In [ ]:
import xarray as xr
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
import cartopy.feature as cfeature
from metpy import calc as mpcalc
from metpy.units import units
import metpy
import numpy as np
from datetime import datetime, timedelta

## Access the ARCO ERA-5 catalog on Google Cloud

Let's open the **37-level isobaric surfaces reanalysis** Zarr file

In [ ]:
reanalysis = xr.open_zarr(
    'gs://gcp-public-data-arco-era5/ar/1959-2022-full_37-1h-0p25deg-chunk-1.zarr-v2', 
    consolidated=True
)

In [ ]:
reanalysis

In [ ]:
geop = reanalysis.geopotential
temp = reanalysis.temperature

In [ ]:
geop








Select time and level ranges from the dataset.

In [ ]:
nHours = 6 
startTime = datetime(1993,3,13,18)
endTime = startTime + timedelta(hours=nHours)

<div class="alert alert-danger">
    <b>RESTRICT YOUR TIME/LEVEL RANGES!</b> <br>
The full dataset is over 70 TB ... if you try to load in too large a range (or forget to specify the start/stop points), you will likely run out of system memory!
</div>

In [ ]:
geopSub1 = geop.sel(time=slice(startTime, endTime), level=500)
tempSub1 = temp.sel(time=slice(startTime, endTime), level=850)

Convert to dam and deg C.

In [ ]:
Z = mpcalc.geopotential_to_height(geopSub1).metpy.convert_units('dam')

In [ ]:
T = tempSub1.metpy.convert_units('degC')

In [ ]:
Z

In [ ]:
T

## Plot the data using Matplotlib

In [ ]:
projData = ccrs.PlateCarree()

In [ ]:
lons, lats = Z.longitude, Z.latitude

In [ ]:
tLevels = np.arange(-45,39,3)
zLevels = np.arange(468, 606, 6)

In [ ]:
res = '110m'
dpi = 100
fig = plt.figure(figsize=(2048/dpi, 1024/dpi))
ax = plt.subplot(1,1,1,projection=projData, frameon=False)

ax.add_feature(cfeature.COASTLINE.with_scale(res), edgecolor='brown', linewidth=2.5)
ax.add_feature(cfeature.BORDERS.with_scale(res), edgecolor='brown', linewidth=2.5)
ax.add_feature(cfeature.STATES.with_scale(res), edgecolor='brown')

# Temperature (T) contour fills

# Note we don't need the transform argument since the map/data projections are the same, but we'll leave it in
CF = ax.contourf(lons,lats,T,levels=tLevels,cmap=plt.get_cmap('coolwarm'), extend='both', transform=projData) 

# Height (Z) contour lines
CL = ax.contour(lons,lats,Z,zLevels,linewidths=1.25,colors='yellow', transform=projData)
ax.clabel(CL, inline_spacing=0.2, fontsize=8, fmt='%.0f')
fig.tight_layout(pad=.01)


In [ ]:
Z

In [ ]:
Z.isel(time=0)

In [ ]:
res = '110m'
dpi = 100
fig = plt.figure(figsize=(2048/dpi, 1024/dpi))
ax = plt.subplot(1,1,1,projection=projData, frameon=False)

ax.add_feature(cfeature.COASTLINE.with_scale(res), edgecolor='brown', linewidth=2.5)
ax.add_feature(cfeature.BORDERS.with_scale(res), edgecolor='brown', linewidth=2.5)
ax.add_feature(cfeature.STATES.with_scale(res), edgecolor='brown')

# Temperature (T) contour fills

# Note we don't need the transform argument since the map/data projections are the same, but we'll leave it in
CF = ax.contourf(lons,lats,T.isel(time=0),levels=tLevels,cmap=plt.get_cmap('coolwarm'), extend='both', transform=projData) 

# Height (Z) contour lines
CL = ax.contour(lons,lats,Z.isel(time=0),zLevels,linewidths=1.25,colors='yellow', transform=projData)
ax.clabel(CL, inline_spacing=0.2, fontsize=8, fmt='%.0f')
fig.tight_layout(pad=.01)


In [ ]:
lonW, lonE, latS, latN = -130, -60, 20, 55 

lonRange = np.arange(lonW, lonE + 0.1, 0.25)
latRange = np.arange(latS, latN + 0.1, 0.25)

In [ ]:
print(latRange)

In [ ]:
print(lonRange)

In [ ]:
ZSub2 = Z.sel(latitude = latRange, longitude = lonRange)
TSub2 = T.sel(latitude = latRange, longitude = lonRange)

In [ ]:
lats

In [ ]:
lons

In [ ]:
ZSub2 = Z.sel(latitude = latRange, longitude = lonRange)
TSub2 = T.sel(latitude = latRange, longitude = lonRange)

In [ ]:
lonW, lonE, latS, latN = -130, -60, 20, 55 

In [ ]:
Z.latitude

In [ ]:
Z.longitude

In [ ]:
ZSub2 = Z.sel(latitude = latRange, longitude = lonRange)
TSub2 = T.sel(latitude = latRange, longitude = lonRange)

In [ ]:
lonW, lonE, latN, latS = 230, 290, 55, 20 

lonRange = np.arange(lonW, lonE - 0.1, 0.25)
latRange = np.arange(latN, latS - 0.1, -0.25)

In [ ]:
ZSub2 = Z.sel(latitude = latRange, longitude = lonRange)
TSub2 = T.sel(latitude = latRange, longitude = lonRange)

In [ ]:
ZSub2

In [ ]:
projMap = ccrs.LambertConformal(central_longitude=(lonW + lonE) / 2., central_latitude=(latS + latN) / 2.)

In [ ]:
%%time 
res = '50m'
dpi = 100
fig = plt.figure(figsize=(2048/dpi, 1024/dpi))
ax = plt.subplot(1,1,1,projection=projMap)

ax.add_feature(cfeature.COASTLINE.with_scale(res), edgecolor='brown', linewidth=2.5)
ax.add_feature(cfeature.BORDERS.with_scale(res), edgecolor='brown', linewidth=2.5)
ax.add_feature(cfeature.STATES.with_scale(res), edgecolor='brown')

# Temperature (T) contour fills

CF = ax.contourf(lons,lats,T.isel(time=0),levels=tLevels,cmap=plt.get_cmap('coolwarm'), extend='both', transform=projData) 

# Height (Z) contour lines
CL = ax.contour(lons,lats,Z.isel(time=0),zLevels,linewidths=1.25,colors='yellow', transform=projData)
ax.clabel(CL, inline_spacing=0.2, fontsize=8, fmt='%.0f')
fig.tight_layout(pad=.01)


In [ ]:
%%time 
res = '50m'
dpi = 100
fig = plt.figure(figsize=(2048/dpi, 1024/dpi))
ax = plt.subplot(1,1,1,projection=projMap)

ax.set_extent([lonW, lonE, latS, latN], crs=ccrs.PlateCarree())
ax.add_feature(cfeature.COASTLINE.with_scale(res), edgecolor='k', linewidth=2.5)
ax.add_feature(cfeature.BORDERS.with_scale(res), edgecolor='k', linewidth=2.5)
ax.add_feature(cfeature.STATES.with_scale(res), edgecolor='k')

# Temperature (T) contour fills

CF = ax.contourf(TSub2.longitude,TSub2.latitude,TSub2.isel(time=0),levels=tLevels,cmap=plt.get_cmap('coolwarm'), extend='both', transform=projData) 

# Height (Z) contour lines
CL = ax.contour(TSub2.longitude,TSub2.latitude,ZSub2.isel(time=0),zLevels,linewidths=1.25,colors='yellow', transform=projData)
ax.clabel(CL, inline_spacing=0.2, fontsize=14, fmt='%.0f')
fig.tight_layout(pad=.01)
